In [7]:
image = 'cloverleaf.jpeg'

In [8]:
from nltk.corpus import stopwords
sw = stopwords.words("english")
from urllib.request import urlopen
import json

resultSentences = []
labels_corpus = []

url = f"https://hub.xpub.nl/soupboat/generic-labels/get-labels/?image=cloverleaf.jpeg"
response = urlopen(url)
data_json = json.loads(response.read()) 

labels = data_json['labels']


for label in labels:
    sent = label['text'].split()
    labels_corpus.append(sent)
    
print(labels_corpus)

[['It', 'is', 'now', 'commonplace', 'among', 'critical', 'librarians', 'to', 'observe', 'the', 'politics', 'of', 'the', 'organization', 'of', 'knowledge', 'in', 'libraries.', 'We', 'have', 'come', 'to', 'recognize', 'the', 'weight', 'of', 'the', 'problems', 'inherent', 'in', 'organizing', 'materials', 'by', 'subject', 'categories,', 'as', 'well', 'as', 'the', 'ways', 'in', 'which', 'our', 'profession', 'is', 'entangled', 'with', 'government', 'institutions', 'like', 'the', 'Library', 'of', 'Congress,', 'and', 'the', 'implications', 'of', 'the', 'universalization', 'of', 'the', 'white,', 'cis-male,', 'propertied', 'subject', 'across', 'our', 'systems.', 'At', 'the', 'same', 'time,', 'we', 'realize', 'that', 'the', 'labour', 'required', 'to', 'make', 'significant', 'changes', 'is', 'insurmountable,', 'particularly', 'during', 'a', 'moment', 'in', 'which', 'cataloguing', 'departments', 'are', 'shrinking,', 'and', 'that', 'most', 'proposed', '‘solutions’', 'cannot', 'address', 'the', 'most

In [9]:
punctuation = ['.', ',', ';', '(', ')', ':']

# since .split(' ') does not split a word from any punctuation, 
# this function search for any string which last character (word[-1]]) is in the variable 'punctuation';
# if that is the case, the function will remove the last charachter, else it will leave it as it is.
def clean_word(word):
    for character in word:
        if word[-1] in punctuation:
            return word[0:-1]
        if word[0] in punctuation:
            return word[1:]
        else:
            return word



In [10]:
# The arguments in this functions are 2 texts (text_a and text_b) an index for where the text_a starts and an index for where it ends.
def bridge(text_a, text_b, start_a, isLast):
    
    matchFound = 0
    start_next = 0
    
    # for index i in text_a from a given index until the end of text_a
    for i in range(start_a, len(text_a)):
        if matchFound:
            break
            
        # we name word_a the index i in text_a
        word_a = text_a[i]
        # if word_a is not in the given list of stopwords:
        if word_a not in sw:
            # for index j in the entire text_b:
            for j in range(0, len(text_b)):
                
                # we name word_b the word with index j in text_b
                word_b = text_b[j]
                
                # if word_a equals to word_b:
                if clean_word(word_a) == clean_word(word_b):
                    
                    # resultSentences is a list to which the following informations will add up:
                    resultSentences.append({
                        'text': text_a,
                        'start': start_a,
                        'end': i })
                    
                    # if the text in position text_a is the last text to be compared:
                    # the same informations as above will be added, except that there will be no index for its end.
                    if isLast:
                        resultSentences.append({
                            'text': text_b,
                            'start': j,
                            'end': None 
                    })
                    
                    # after the match is found between the 2 texts, the function will break
                    matchFound = 1 
                    start_next = j
                    break
    
    if matchFound == 0:
        resultSentences.append({
            'text': text_a,
            'start': start_a,
            'end': None
        })
        
        if isLast:
            resultSentences.append({
                'text': text_b,
                'start': 0,
                'end': None 
        })

                        
    # the function returns the index of the 'same word' in the text_b
    return start_next


In [11]:
def bridge_list(corpus):
    start_a = 0
    result = ""
    
    #for all texts indexes within the corpus to be compared:
    for text_index in range(0, len(corpus)-1):

        # the last text_a to be compared has to be the text indexed as corpus[-2];
        # the last text_b will then be the last text of the corpus (corpus[-1]).
        isLast = text_index == len(corpus)-2
        # text_a is a given index of the corpus and text_b is the following index
        text_a = corpus[text_index]
        text_b = corpus[text_index + 1]
            
    
        #start_a is the index (in text_b) of the first 'common word' between text_a and text_b;
        #start_a is the starting point to compare a text and its following (in index order within the corpus); 

        start_next = bridge(text_a, text_b, start_a, isLast)
        start_a = start_next
    

In [12]:
bridge_list(labels_corpus)

endResult = ''
for i in range(0, len(resultSentences)):
    sentence = resultSentences[i]
    start = sentence['start']
    end = sentence['end']
    sentenceText = sentence['text']
    
    endResult = endResult + " " + " ".join(sentenceText[start:end])
    
print(endResult)

 It is now commonplace among critical librarians to observe the  politics of location as a form of situated dwelling (Lorde 1984; Rich1986; Haraway 1991; Collins 1998), and to the black feminist writers who havestaged the impossible, that under this condition alone does the living pre- serve itself and flourish.”7
